#### import required packages 

In [1789]:
import numpy as np
import pandas as pd

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt
from statsmodels.graphics.gofplots import qqplot

from itertools import islice
from random import randint

from scipy.optimize import minimize
import autograd.numpy as np
from autograd_gamma import gammaln

In [1790]:
def scientific_notation(lst):
    vals = ['{:.2e}'.format(i) for i in list(lst)]
    print(tuple(vals))

#### sampled residuals with outliers

In [1791]:
def generate(median, err, outlier_err, size, outlier_size):
    errs = err * np.random.standard_normal(size) * np.random.choice((-1, 1), size)
    data = median + errs
    
    lower_errs = outlier_err * np.random.standard_normal(outlier_size)
    lower_outliers = median - err - lower_errs

    upper_errs = outlier_err * np.random.standard_normal(outlier_size)
    upper_outliers = median + err + upper_errs

    data = np.concatenate((data, lower_outliers, upper_outliers))
    np.random.shuffle(data)

    return data

In [1792]:
first_data = []
for i in range(0, 250):
    first_data.append(generate(median=0, err=0.02, outlier_err=0.01, size=5, outlier_size=1))
    
second_data = []
for i in range(0, 250):
    second_data.append(generate(median=0, err=0.2, outlier_err=0.1, size=50, outlier_size=10))

# third_data = []
# for i in range(0, 300):
#     third_data.append(generate(median=3, err=1.5, outlier_err=10, size=40, outlier_size=0))
    
# forth_data = []
# for i in range(0, 300):
#     forth_data.append(generate(median=3, err=1.5, outlier_err=10, size=40, outlier_size=5))

In [1772]:
def equal_chunking(lst, n):
    for i in range(0, len(lst), n):
        yield lst[i:i + n]
        
def random_chunking(lst, min_chunk, max_chunk):
    lst = iter(lst)
    while True:
        nxt = list(islice(lst,randint(min_chunk,max_chunk)))
        if nxt:
            yield nxt
        else:
            break

In [1773]:
full_lst = first_data + second_data 
# + third_data + forth_data
full_lst = [arr.tolist() for arr in full_lst]

# full_lst = sorted(full_lst, key=lambda k: random.random())

#### simulated data

In [1208]:
def simulated_data(beta0, sigmaXi, sigmaU, T, a_size):
    a = [np.ones(a_size).astype(int) for i in range(T)]
    # a = [np.ones(10).astype(int) for i in range(T)]
    xi = np.random.normal(loc=0,scale=1,size=T) * sigmaXi
    eta = []
    eta.append(np.zeros(len(a[0])))
    u = [np.zeros(len(a[i])) for i in range(T)]
    beta = np.empty(T)
    beta[0] = beta0
    for i in range(1, T):
        beta[i] = beta[i-1] + xi[i]
        u[i] = np.random.normal(loc=0,scale=1,size=len(a[i])) * sigmaU
        eta.append(np.array(beta[i] * a[i] + u[i]))
    return(beta[1:], eta[1:])
aa = simulated_data(beta0=0, sigmaXi=0.01, sigmaU=0.02, T=500, 
                    a_size=50)
# randint(5,20)
# bb = simulated_data(aa[1][-1], 0.01, 0.04, 101)

In [1209]:
full_lst = [arr.tolist() for arr in aa[1]] 
# + [arr.tolist() for arr in bb[2]][1:]
dates = [*range(1, len(full_lst)+1)]

In [1210]:
full_lst_flatten = [i for sublist in full_lst for i in sublist]

### real data

In [1802]:
heck_df = pd.read_csv('heck.csv', delimiter=',')
full_lst = []
for i in range(1, max(heck_df['precision'])):
    ls = list(heck_df.loc[heck_df['precision'] == i]['Heckman_result_withouttime'])
    full_lst.append(ls)
dates = list(heck_df['dates'].drop_duplicates(keep='first'))

#### dcs-t filtering

In [1803]:
class DCSt_filtering(object):
    def __init__(self, llst_resid):        
        self.resid_lst = llst_resid
        self.resid_arr = []
        self.Time = len(llst_resid)
        self.precision = []
        self.n_t = []
        self.n_t = []
        self.Beta = []
        self.a = []
        
    def DataPreparation(self):
        for i in range(0, self.Time):
            self.precision.append((np.ones(len(self.resid_lst[i])) * (i+1)).astype(int))
        self.precision = [arr.tolist() for arr in self.precision]
        self.precision = np.array([i for sublist in self.precision for i in sublist])
        self.resid_arr = np.array([i for sublist in self.resid_lst for i in sublist])
        
        for i in range(0, self.Time):
            logi1 = np.array(self.precision == i+1).astype(int)
            self.n_t.append(sum(logi1))
            self.Beta.append((1/self.n_t[i]) * np.dot(self.resid_arr, logi1))
            self.a.append(logi1)
        self.a = np.stack(self.a)
        
    def computeLikelihood(self, params):
        sigmaVsq, kappa ,nu = params
        u = np.zeros(self.Time)
        likLi = []
        for i in range(1, self.Time):
            previous = np.where(self.precision==i)
            aPrevious = self.a[i-1][previous]
            aPreviousT = aPrevious.T
            
            etaPrevious = np.dot(aPrevious, self.Beta[i-1])
            
            ePrevious = self.resid_arr[previous] - etaPrevious

            ePreviousT = ePrevious.T
            nSp_pre = self.n_t[i-1]
            
            self.Beta[i] = self.Beta[i-1] + kappa * u[i-1]
            
            w = 1 + (1 / (nu*sigmaVsq)) * np.dot(ePrevious, ePreviousT)
            u[i] = (1 / w) * ((nu+nSp_pre) / nu) * (1/sigmaVsq) * np.dot(aPreviousT, ePrevious)
            
            likLi.append(gammaln((nu+nSp_pre)/2)-gammaln(nu/2)-(nSp_pre/2)*np.log(np.pi*nu* sigmaVsq)-(nu+nSp_pre)/2 * np.log(w))
            
        return -1*sum(likLi)
    
    def updateBeta(self, params):
        sigmaVsq, kappa ,nu = params
        u = np.zeros(self.Time)
        for i in range(1, self.Time):
            previous = np.where(self.precision==i)
            aPrevious = self.a[i-1][previous]
            aPreviousT = aPrevious.T
            
            etaPrevious = np.dot(aPrevious, self.Beta[i-1])
            
            ePrevious = self.resid_arr[previous] - etaPrevious
            ePreviousT = ePrevious.T
            nSp_pre = self.n_t[i-1]
            
            self.Beta[i] = self.Beta[i-1] + kappa * u[i-1]
            
            w = 1 + (1 / (nu*sigmaVsq)) * np.dot(ePrevious, ePreviousT)
            u[i] = (1 / w) * ((nu+nSp_pre) / nu) * (1/sigmaVsq) * np.dot(aPreviousT, ePrevious)
        return self.Beta, u
        

In [1804]:
run_dcs_t = DCSt_filtering(full_lst)
run_dcs_t.DataPreparation()

In [1808]:
history_dcs_t=[]
def callback(x):
    fobj = run_dcs_t.computeLikelihood(x)
    history_dcs_t.append(fobj)

opt_dcs_t = minimize(fun=run_dcs_t.computeLikelihood,
               x0=[1, 0.0001, 3],
               bounds=([0,None], [0, None], [2.1, None]),
               method='Nelder-Mead',
               tol=1e-2,
               callback=callback,
               options={'disp': True, 'return_all': True})

Optimization terminated successfully.
         Current function value: 231796.495998
         Iterations: 45
         Function evaluations: 86


In [1809]:
opt_dcs_t.x

array([9.69606631e-01, 9.07949315e-04, 2.10000000e+00])

In [1810]:
beta_dcs_t = run_dcs_t.updateBeta(opt_dcs_t.x)
# [6.11677448e-02, 1.80964193e-03, 3.72612639e+01]

#### Kalman filtering

In [1811]:
class kalman_filtering(object):
    def __init__(self, llst_resid):
        self.resid_lst = llst_resid
        self.resid_arr = []
        self.Time = len(llst_resid)
        self.precision = []
        self.n_t = []
        self.n_t = []
        self.Beta = []
        self.a = []
        self.sigmaUsq = []
        self.sigmaXiSqOLS = []
        self.sigmaBSq = []
        self.zeta = []
        
    def DataPreparation(self):
        for i in range(0, self.Time):
            self.precision.append((np.ones(len(self.resid_lst[i])) * (i+1)).astype(int))
        self.precision = [arr.tolist() for arr in self.precision]
        self.precision = np.array([i for sublist in self.precision for i in sublist])
        self.resid_arr = np.array([i for sublist in self.resid_lst for i in sublist])
        
        resSq = []
        n_t_inv = []
        for i in range(0, self.Time):
            logi1 = np.array(self.precision == i+1).astype(int)
            self.n_t.append(sum(logi1))
            n_t_inv.append(1/self.n_t[i])
            self.Beta.append((1/self.n_t[i]) * np.dot(self.resid_arr, logi1))
            resSq.append(np.square(np.dot(self.resid_arr, logi1) - self.Beta[i]))
            self.a.append(logi1)
        self.a = np.stack(self.a)
        
        xi = np.array(self.Beta[1:]) - np.array(self.Beta[0:self.Time-1])
        self.sigmaUsq = (1/(1-1/self.Time * sum(n_t_inv))) * (1/self.Time) * np.dot(n_t_inv, resSq)
        self.sigmaXiSqOLS = ((self.Time-1)/self.Time) * np.var(xi) - self.sigmaUsq * 1/self.Time * sum(n_t_inv)
        self.sigmaBSq = (self.Time-1)/self.Time * np.dot(np.var(self.Beta), np.repeat(1, self.Time)) 
        self.zeta = np.dot(self.sigmaXiSqOLS, np.repeat(1, self.Time)) + self.sigmaBSq

    def computeLikelihood(self, sigmaXiSq):
        likLi = []
        for t in range(1, self.Time):
            # prediction step
            current = np.where(self.precision==t+1)
            aCurrent = self.a[t][current]
            aTranspose = aCurrent.T
            nSp = self.n_t[t]
            
            self.Beta[t] = self.Beta[t-1]
            
            self.sigmaBSq[t] = self.sigmaBSq[t-1] + sigmaXiSq
            sigmaEtaSq = aCurrent.dot(self.sigmaBSq[t]).dot(aTranspose) + self.sigmaUsq * np.identity(nSp)
            
            etaCurrent = np.dot(aCurrent, self.Beta[t])
            e_t = self.resid_arr[current] - etaCurrent
            
            m = 10^-6
            self.Beta[t] = self.Beta[t]+ np.dot(self.sigmaBSq[t], aTranspose).dot(np.linalg.inv(sigmaEtaSq+ np.eye(sigmaEtaSq.shape[1])*m)).dot(e_t)
            
            self.sigmaBSq[t] = self.sigmaBSq[t] - (np.square(self.sigmaBSq[t]) * aTranspose).dot(np.linalg.inv(sigmaEtaSq)).dot(aCurrent)
            
            self.zeta[t] = self.sigmaBSq[t] + sigmaXiSq
            zetaTT_1 = self.zeta[t-1]
            sigma_t_zeta = abs(2*(nSp-1) * np.log(np.sqrt(self.sigmaUsq))  + np.log(nSp*zetaTT_1+self.sigmaUsq))
            
            sigma_t_1_zeta = 1/(nSp*zetaTT_1+self.sigmaUsq)*np.dot(aCurrent,aTranspose)/nSp + 1/self.sigmaUsq*(np.identity(nSp)-np.dot(aCurrent,aTranspose)/nSp)
            
            likLi.append(0.5 * (sigma_t_zeta + e_t.dot(sigma_t_1_zeta).dot(e_t.T)))
        return sum(likLi)
    
    def updateBeta(self, sigmaXiSq):
        for i in range(1, self.Time): 
            current = np.where(self.precision==i+1)
            aCurrent = self.a[i][current]
            
            self.Beta[i] =  self.Beta[i-1]
            self.sigmaBSq[i] = self.sigmaBSq[i-1] + sigmaXiSq
            
            etaCurrent = np.dot(aCurrent, self.Beta[i])
            e_t = self.resid_arr[current] - etaCurrent
            nSp = self.n_t[i]
            aTranspose = aCurrent.T
            
            sigmaEtaSq = aCurrent.dot(self.sigmaBSq[i]).dot(aTranspose) + self.sigmaUsq * np.identity(nSp)
            
            m = 10^-6
            self.Beta[i] = self.Beta[i] + np.dot(self.sigmaBSq[i], aTranspose).dot(np.linalg.inv(sigmaEtaSq+ np.eye(sigmaEtaSq.shape[1])*m)).dot(e_t)
            
            self.sigmaBSq[i] = self.sigmaBSq[i] - (np.square(self.sigmaBSq[i]) * aTranspose).dot(np.linalg.inv(sigmaEtaSq)).dot(aCurrent)

        return self.Beta        

In [1812]:
run_kf = kalman_filtering(full_lst)
run_kf.DataPreparation()

In [1814]:
history_kf=[]
def callback(x):
    fobj = run_kf.computeLikelihood(x)
    history_kf.append(fobj)

opt_kf = minimize(fun=run_kf.computeLikelihood,
               x0=0.5,
               method='Nelder-Mead',
               tol=1e-5,
               bounds=[(0,None)],
               callback=callback,
               options={'disp': True, 'return_all': True})

Optimization terminated successfully.
         Current function value: 35035.610783
         Iterations: 20
         Function evaluations: 45


In [1815]:
opt_kf.x

array([0.52788086])

In [1816]:
beta_kf = run_kf.updateBeta(opt_kf.x)


In [1817]:
dates = list(range(1, len(full_lst)+1))
df_resid = pd.DataFrame()
df_resid['resid'] = [i for sublist in full_lst for i in sublist]
df_resid['dates'] = run_dcs_t.precision

#### compare

In [1818]:
index_dcs_t = np.exp(beta_dcs_t[0])/np.exp(beta_dcs_t[0][0])
index_kf = np.exp(beta_kf)/np.exp(beta_kf[0])


In [1819]:
from sklearn.metrics import mean_squared_error
mse_dcs_t = mean_squared_error(aa[0].tolist(), beta_dcs_t[0], 
                               squared=True)
mse_kf = mean_squared_error(aa[0].tolist(), beta_kf, squared=True)
print('{:.2e}'.format(mse_kf), '{:.2e}'.format(mse_dcs_t))

ValueError: Found input variables with inconsistent numbers of samples: [499, 960]

In [1820]:
#### test
dates = list(range(1, len(full_lst)+1))
# beta_dcs_t = run_dcs_t.updateBeta([1.18567725e+00, 9.05355033e-04, 8.81525824e+00])
# [1.18567725e+00, 9.05355033e-04, 8.81525824e+00]
# [3, 9.05355033e-04, 8.81525824e+00]

In [1824]:

fig = make_subplots(specs=[[{"secondary_y": True}]])
                    
fig['layout'].update(height=800, width=1600,
                    title='',
                    showlegend=False,
                    font=dict(family='Times New Roman', size=10))

fig.add_trace(go.Box(x=df_resid['dates'], 
                     y=df_resid['resid'], 
                     notched=False,
                     line=dict(color='#7EC8E3', width=0.5),
                     marker=dict(size=2)),
              secondary_y=False)

fig.add_trace(go.Scatter(x=dates, 
                         y=aa[0].tolist(), 
                         line=dict(color='green', dash='dash', width=1.5)),
              secondary_y=True)
# fig.add_trace(go.Scatter(x=dates, 
#                          y=beta_dcs_t[0],  
#                          line=dict(color='red', dash='solid', width=1.5) ),
#               secondary_y=True)
# fig.add_trace(go.Scatter(x=dates, 
#                          y=beta_kf, 
#                          line=dict(color='blue', dash='dot', width=1.5)),
#               secondary_y=True)

# fig.add_trace(go.Scatter(x=dates, 
#                          y=np.exp(aa[0].tolist())/np.exp(aa[0].tolist()[0]), 
#                          line=dict(color='green', dash='dash', width=1.5)),
#               secondary_y=True)
fig.add_trace(go.Scatter(x=dates, 
                         y=index_dcs_t,  
                         line=dict(color='red', dash='solid', width=1.5) ),
              secondary_y=True)

fig.add_trace(go.Scatter(x=dates, 
                         y=index_kf, 
                         line=dict(color='blue', dash='dot', width=1.5)),
              secondary_y=True)



fig.update_xaxes(showline=True, linewidth=1, linecolor='black', 
                 mirror=True,
                 showgrid=False,
                 dtick = 10)
fig.update_yaxes(showline=True, linewidth=1, 
                 linecolor='black', 
                 mirror=True, 
                 showgrid=False)

fig['layout']['xaxis'].update(title='Time')

# fig.update_xaxes(showline=True, linewidth=1, linecolor='black', 
#                  mirror=True,
#                  tickformat="%b\n%Y", 
#                  showgrid=False,
#                  dtick = 'M1')

fig.update_layout({'plot_bgcolor': 'rgba(0,0,0,0)',
                   'paper_bgcolor': 'rgba(0,0,0,0)'},
                  font_color='black',
                  bargap=0,
                  yaxis=dict(title_text='Residual', 
                             side='right'
                             ),
                  yaxis2=dict(title_text='&#946;',
                              side='left'))

fig.update_layout(bargap=0)


fig.show()
# fig.write_image('images/outlier_1z.pdf')




#### qq plot

In [334]:
qqplot_data = qqplot(np.array(full_lst_flatten), line='s').gca().lines
plt.close()
fig = make_subplots(specs=[[{"secondary_y": False}]])
fig['layout'].update(height=400, width=400,
                         title='',
                         showlegend=False,
                         font=dict(family='Times New Roman', size=12))
fig.add_trace(go.Scatter(
    y=qqplot_data[0].get_ydata(),
    x=qqplot_data[0].get_xdata(),
    mode='markers', 
    marker=dict(color='white', line=dict(color='black', width=1))  
    ), secondary_y=False)

fig.add_shape(type='line',
            yref='paper', xref='paper',
            y0=0, y1=1, x0=0, x1=1,
            line=dict(color='blue'))

fig['layout']['xaxis'].update(title='Theoretical quantiles')
fig['layout']['yaxis'].update(title='Sample quantiles')

fig.update_xaxes(showline=True, linewidth=1, linecolor='black',
                 mirror=True,
                 showgrid=False)
fig.update_yaxes(showline=True, linewidth=1, linecolor='black', 
                 mirror=True, 
                 showgrid=False)


fig.update_layout({'plot_bgcolor': 'rgba(0,0,0,0)',
                'paper_bgcolor': 'rgba(0,0,0,0)'},
                font_color='black')

fig.show()